# Write a Python program that filters out exactly and/or semantically duplicate articles from your Webhose dataset of news articles:

## Use LSH (SimHash or MinHash), separately or along with Word2Vec, to deduplicate your Webhose feeds based on titles


## Make sure to store entire feeds in a JSON, text or CSV file


## Your final submission should include the Jupyter Notebook with the original set of titles and a deduplicated subset of titles

In [5]:
#!pip install simhash

  Created wheel for simhash: filename=simhash-1.9.0-cp37-none-any.whl size=3227 sha256=4546a4bafa71f4e654253248a3d18ef47a54f60e71dbb7ee85c76ff27ff165bc
  Stored in directory: /Users/matthewvitha/Library/Caches/pip/wheels/06/97/9d/29034ef078c26e0a5b5a789e7bd8f90a8f0c2f3bd95f511ca1
Successfully built simhash


In [1]:
import webhoseio, os
from gensim.models import KeyedVectors
import json
from simhash import Simhash, SimhashIndex
import numpy as np

In [2]:
import pickle 
filehandler = open('apanps5430_webhose.pickle', 'rb') 
object1 = pickle.load(filehandler)

In [3]:
len(object1)

10300

In [3]:
model_path = '/Users/matthewvitha/Downloads/'

# Load Model and Use Functions Defined From In Class Exercise

In [4]:

def load_wordvec_model(modelName, modelFile, flagBin):
    print('Loading ' + modelName + ' model...')
    model = KeyedVectors.load_word2vec_format(model_path + modelFile, binary=flagBin)
    print('Finished loading ' + modelName + ' model...')
    return model

In [5]:
model_w2v_AP    = load_wordvec_model('Word2Vec Google News', 'GoogleNews-vectors-negative300.bin.gz', True)


Loading Word2Vec Google News model...
Finished loading Word2Vec Google News model...


In [4]:
# function checks whether the input words are present in the vocabulary for the model
def vocab_check(vectors, words):
    
    output = list()
    for word in words:
        if word in vectors.vocab:
            output.append(word.strip())
            
    return output

In [5]:
# function calculates similarity between two strings using a particular word vector model
def calc_similarity(input1, input2, vectors):
    s1words = set(vocab_check(vectors, input1.split()))
    s2words = set(vocab_check(vectors, input2.split()))
    
    output = vectors.n_similarity(s1words, s2words)
    return output

In [6]:
def cleanup(input):
    # remove English stopwords
    input = input.replace("'s", " ").replace("n’t", " not").replace("’ve", " have")
    input = re.sub(r'[^a-zA-Z0-9 ]', '', input)
    return input

In [7]:
object1[0]['title']

'BHP reviews lobby group membership amid investor climate push'

In [8]:
object1[10299]

{'thread': {'uuid': '5639e826c591de6d07a740f3fe1d5ac7172d6b68',
  'url': 'http://www.baystreet.ca/viewarticle.aspx?id=559527',
  'site_full': 'www.baystreet.ca',
  'site': 'baystreet.ca',
  'site_section': 'http://www.baystreet.ca/publish.aspx',
  'site_categories': ['financial_news', 'finance'],
  'section_title': 'Baystreet.ca - ACCESSWIRE ',
  'title': 'Cub Energy Announces Spudding of First of Three Wells in Western Ukraine',
  'title_full': 'Cub Energy Announces Spudding of First of Three Wells in Western Ukraine',
  'published': '2019-09-16T15:30:00.000+03:00',
  'replies_count': 0,
  'participants_count': 1,
  'site_type': 'news',
  'country': 'CA',
  'spam_score': 0.151,
  'main_image': '',
  'performance_score': 0,
  'domain_rank': None,
  'social': {'facebook': {'likes': 0, 'comments': 0, 'shares': 0},
   'gplus': {'shares': 0},
   'pinterest': {'shares': 0},
   'linkedin': {'shares': 0},
   'stumbledupon': {'shares': 0},
   'vk': {'shares': 0}}},
 'uuid': '5639e826c591de6d07

# Print index and article title for each article in corpus

In [152]:
[sorted(x.items(), key=operator.itemgetter(1)) for x in range(len(object1[i]))]


AttributeError: 'int' object has no attribute 'items'

# John notes - check up front to make sure that there are duplicates and if not, FORCE THEM IN TO MAKE SURE WE CAN ACTUALLY DEDUPE 

# show the sort


In [ ]:
[sorted(x.items(), key=operator.itemgetter(1)) for x in range(len(object1[i]))]
### forcefully put in 20 more articles 

In [ ]:
for i in range(len(object1)):
    print(i,":",object1[i]['title'],object1[i]['url'])

In [10]:
for i in range(len(object1)):
    print(i,":",object1[i]['title'],object1[i]['url'])

0 : BHP reviews lobby group membership amid investor climate push https://fntalk.com/companies/bhp-reviews-lobby-group-membership-amid-investor-climate-push/
1 :  https://www.theguardian.com/commentisfree/2019/sep/05/trump-emoluments-corruption-mike-pence-hotel#132796074
2 : U.S., Chinese envoys to meet in October for tariff war talks http://lasvegassun.com/news/2019/sep/05/us-chinese-envoys-to-meet-in-october-for-tariff-wa/
3 :  https://www.marketwatch.com/story/the-explosion-of-alternative-data-gives-regular-investors-access-to-tools-previously-employed-only-by-hedge-funds-2019-09-05#ab0e2be5124bf43b2890ba3de217a49a
4 :  https://www.breitbart.com/the-media/2019/09/05/cnn-map-mislabels-alabama-as-mississippi-in-hurricane-dorian-coverage/#post-43
5 : Boxwood Merger, Atlas Technical Consultants combine businesses https://financial-news.co.uk/boxwood-merger-atlas-technical-consultants-combine-busi/
6 : OCC Fined by SEC/CFTC; CME’s Bitcoin Options(?!) https://johnlothiannews.com/occ-fined

429 : U.S.-China Plan Oct Trade Talks | Industrial Equipment News (IEN) https://www.ien.com/supply-chain/news/21085661/uschina-plan-oct-trade-talks
430 : U.S jobs data supports dollar as fragile risk-on mood holds https://www.theedgemarkets.com/article/us-jobs-data-supports-dollar-fragile-riskon-mood-holds
431 : US, Chinese envoys to meet in October for tariff war talks http://www.chroniclejournal.com/news/world/us-chinese-envoys-to-meet-in-october-for-tariff-war/article_2047b49a-5b03-5045-967d-31c4da0fce5e.html
432 : Japan July preliminary leading indicator index 93.6 vs 93.2 expected https://www.forexlive.com/news/!/japan-july-preliminary-leading-indicator-index-vs-932-expected-20190906
433 : Asian Markets Extend Gains http://markets.businessinsider.com/news/stocks/asian-markets-extend-gains-1028503906
434 : Cari film semi Austria Jerman tentang wanita cantik muda https://chirpstory.com/li/443773
435 : US, Chinese envoys to meet in October for tariff war talks https://www.newschief.c

929 : U.S. Stocks Edge Up After Jobs Report https://www.marketscreener.com/news/markets/news/U-S-Stocks-Edge-Up-After-Jobs-Report--29169221/
930 : Brexit latest news: Rebel bill passes in the Lords and heads for Royal Assent as opposition leaders vow to reject Boris Johnson's election bid https://www.telegraph.co.uk/politics/2019/09/06/brexit-latest-news-boris-johnson-no-deal-bill-general-election?playlist=structure%3Anews%2Fuk-news
931 : Postmates Charmed Hollywood. Now The $1.85 Billion Delivery Startup Needs To Win Over Everyone Else. https://www.forbes.com/sites/bizcarson/2019/09/06/postmates-charmed-hollywood-before-ipo/?utm_source=TWITTER&utm_medium=social&utm_term=Carrie/
932 : Tiger Global extends gains https://www.opalesque.com/fullarticle/675241/Tiger_Global_extends_gains524.html
933 : What will be the economic backdrop for the 2020 election? New data gives hints http://www.msn.com/en-us/money/markets/what-will-be-the-economic-backdrop-for-the-2020-election-new-data-gives-hin

1554 : USA Financial Portformulas Corp Boosts Holdings in Vanguard Total Stock Market ETF (NYSEARCA:VTI) https://www.americanbankingnews.com/2019/09/07/usa-financial-portformulas-corp-boosts-holdings-in-vanguard-total-stock-market-etf-nysearcavti.html
1555 :  http://www.bangaloremirror.com/bangalore/others/hal-completes-trials-of-2-aircraft/articleshow/71000733.cms#post-8
1556 : The U.S. Navy's Montana-Class Battleships Would Have Been A True Terror http://conservativeangle.com/the-u-s-navys-montana-class-battleships-would-have-been-a-true-terror/
1557 : Pagerduty’s Jennifer Tejada and Box’s Aaron Levie will talk IPOs at TC Disrupt SF https://xtechnews.com/2019/09/06/pagerdutys-jennifer-tejada-and-boxs-aaron-levie-will-talk-ipos-at-tc-disrupt-sf/
1558 : Rebound Predicted For Malaysia Stock Market https://www.rttnews.com/3028147/rebound-predicted-for-malaysia-stock-market.aspx
1559 : South Korea Bourse May Extend Winning Streak https://www.rttnews.com/3028146/south-korea-bourse-may-exte

2178 : Share Watch- Husqvarna harvests a return from stress-free gardening https://www.independent.ie/business/world/share-watch-husqvarna-harvests-a-return-from-stressfree-gardening-38414604.html
2179 : Oil giant Saudi Aramco taps boutique banks for advice ahead of its IPO https://www.independent.ie/business/world/oil-giant-saudi-aramco-taps-boutique-banks-for-advice-ahead-of-its-ipo-38421379.html
2180 : Does trusted 'barometer' show a global recession is imminent&quest; https://www.independent.ie/business/world/does-trusted-barometer-show-a-global-recession-is-imminent-38432999.html
2181 : Recession in India… R U Investing in DEAD? https://www.thewealthwisher.com/recession-in-india/
2182 : Falih replaced as Saudi Oil Minister by Prince Abdulaziz https://www.upstreamonline.com/live/1847744/falih-replaced-as-saudi-oil-minister-by-prince-abdulaziz
2183 : The New England Patriots Decision To Acquire Antonio Brown Explained In Seven Warren Buffett Quotes https://www.forbes.com/sites/ianma

...

8052 : Investor Corner: Performance Watch for MyoKardia, Inc. (NASDAQ:MYOK) https://osburnoracle.com/investor-corner-performance-watch-for-myokardia-inc-nasdaqmyok/232469/
8053 : Keeping Tabs on Shares of Belden Inc. (NYSE:BDC) https://osburnoracle.com/keeping-tabs-on-shares-of-belden-inc-nysebdc/232490/
8054 : My Turn: Why Uncle Sam shouldn't pay off college debt https://www.gastongazette.com/entertainmentlife/20190913/my-turn-why-uncle-sam-shouldnt-pay-off-college-debt
8055 : Global Cons Staples Ishares ETF (KXI) A Look Inside the Technicals https://osburnoracle.com/global-cons-staples-ishares-etf-kxi-a-look-inside-the-technicals/233496/
8056 : NextEra Energy Partners, LP (NYSE:NEP): How is This Stock Looking? https://osburnoracle.com/nextera-energy-partners-lp-nysenep-how-is-this-stock-looking/232393/
8057 : Investor Watch: Focusing on Shares of Tower Semiconductor Ltd. (NASDAQ:TSEM) https://osburnoracle.com/investor-watch-focusing-on-shares-of-tower-semiconductor-ltd-nasdaqtsem/232

8552 : J.Crew's Madewell brand files for IPO https://my.gvtc.com/news/read/category/news/article/the_associated_press-jcrews_madewell_brand_files_for_ipo-ap
8553 : US stock indexes end mixed; S&P 500 notches 3rd weekly gain https://my.gvtc.com/news/read/category/news/article/the_associated_press-us_stocks_are_mixed_as_health_care_gains_tech_drop-ap
8554 : McClatchy's losses, debt put its stock exchange listing at risk https://www.bizjournals.com/sacramento/news/2019/09/13/mcclatchys-losses-debt-put-its-stock-exchange.html
8555 : Awesome Oscillator Ticks Up to 2.93257588 on Shares of Fortune Brands Home & Security, Inc. ($NYSE:FBHS) as Investors Circle https://osburnoracle.com/awesome-oscillator-ticks-up-to-2-93257588-on-shares-of-fortune-brands-home-security-inc-nysefbhs-as-investors-circle/233772/
8556 : Watching the Technicals for Southern Copper Corporation (NYSE:SCCO): Moving Average Rating at Strong Buy https://osburnoracle.com/watching-the-technicals-for-southern-copper-corporati

9052 : SIP: Propaganda! Ignore click-bait headlines about problems in SIPs - The Economic Times https://economictimes.indiatimes.com/markets/stocks/news/propaganda-ignore-click-bait-headlines-about-problems-in-sips/articleshow/71105337.cms
9053 : Yemeni Rebel Drones Spark Fires at Two Saudi Aramco Oil Factories http://www.naharnet.com/stories/en/264752-yemeni-rebel-drones-spark-fires-at-two-saudi-aramco-oil-factories
9054 : HK exchange vows to press on with $39 billion LSE bid https://www.gulftoday.ae/business/2019/09/14/hk-exchange-vows-to-press-on-with-$39-billion-lse-bid
9055 : Americas newest stock exchange wants to fix one of capitalisms fundamental challenges https://www.vox.com/recode/2019/5/22/18629621/long-term-stock-exchange-explainer-capitalism-quarterly-earnings
9056 : Tech shares weigh on stock market; car sales drive retail sales higher https://www.postandcourier.com/tech-shares-weigh-on-stock-market-car-sales-drive-retail/article_6e0c5752-d624-11e9-bde3-b75f7daa4fa0.html

9552 : Luxury’s Trouble Getting Down With American Kids https://www.wsj.com/articles/luxurys-trouble-getting-down-with-american-kids-11568559721
9553 : Are Penny Stocks Worth It? https://pennystocks.com/featured/2019/09/15/are-penny-stocks-worth-it/
9554 : Will The Fed Rate Cut Stall The Market's Rally? https://www.forbes.com/sites/tomaspray/2019/09/15/will-the-fed-rate-cut-stall-the-markets-rally/
9555 : Could Be "Weeks" Before Aramco Restores Full Production Capacity As Specter Of $100 Oil Looms http://conservativeangle.com/could-be-weeks-before-aramco-restores-full-production-capacity-as-specter-of-100-oil-looms/
9556 : Beyond Meat investor warns company's $9bn valuation could be a bubble waiting to burst https://www.telegraph.co.uk/technology/2019/09/15/beyond-meat-investor-warns-companys-9bn-valuation-could-bubble/
9557 : Beyond the hype: Is Beyond Meat's plant-based burger just a bubble? https://www.telegraph.co.uk/technology/2019/09/15/beyond-meat-chairman-just-bubble/
9558 : Do

10059 : Investigation of drone attacks on Saudi oil facilities still on https://www.newkerala.com/news/read/212031/investigation-of-drone-attacks-on-saudi-oil-facilities-still-on.html
10060 : EUR/USD Tested 1.1112 Resistance | Action Forex https://www.actionforex.com/contributors/fundamental-analysis/233753-eur-usd-tested-1-1112-resistance/
10061 : Oil soars after Saudi facility attacks, weak China data hits shares https://www.timeslive.co.za/sunday-times/business/2019-09-16-oil-soars-after-saudi-facility-attacks-weak-china-data-hits-shares
10062 : Europe: Stock markets fall at open, Stocks - THE BUSINESS TIMES https://www.businesstimes.com.sg/stocks/europe-stock-markets-fall-at-open-16
10063 : Asian markets mixed as oil prices surge http://brooklyn.news12.com/story/41050553/asian-markets-mixed-as-oil-prices-surge
10064 : Asian markets mixed as oil prices surge https://www.baynews9.com/fl/tampa/ap-top-news/2019/09/16/asian-markets-mixed-as-oil-prices-surge0
10065 : Asian markets mixed 

# Given that we are using Simhash rather than Minhash, we will use a Hamming Distance of 10. Jaccard Similarity exists as a fraction between 0 and 1. 

# A distance of 10 is used because given sensitivies around markets, timing, and small but different articles (i.e. bought 100 shares vs bought 10000 shares is a big difference), I wanted to use a high threshold for de_duping articles

# John Notes - simhash and minhash ... aim is to whenever u use a hash object, using a hashing algorithm for deduplication is gonna be grabbing unique keys 


# every object in the simhash should be deduped

# could have two articles that have different simhash id's .... for every title .... if i pass the same titles it should have the same simhash  

In [11]:
distance = 10
objs = [(str(i), Simhash(str(object1[i]['title']))) for i in range(len(object1))]
index = SimhashIndex(objs, k=distance)

In [12]:
objs

[('0', <simhash.Simhash at 0x1a21c4cb38>),
 ('1', <simhash.Simhash at 0x1a21c4c400>),
 ('2', <simhash.Simhash at 0x1a21c4cc18>),
 ('3', <simhash.Simhash at 0x1a21c4ceb8>),
 ('4', <simhash.Simhash at 0x1a21c4cd68>),
 ('5', <simhash.Simhash at 0x1a21c4c8d0>),
 ('6', <simhash.Simhash at 0x1a21c4c0f0>),
 ('7', <simhash.Simhash at 0x1a21c4cf60>),
 ('8', <simhash.Simhash at 0x1a21c4cd30>),
 ('9', <simhash.Simhash at 0x1a21c64048>),
 ('10', <simhash.Simhash at 0x1a21c64588>),
 ('11', <simhash.Simhash at 0x1a21c641d0>),
 ('12', <simhash.Simhash at 0x1a21c64ac8>),
 ('13', <simhash.Simhash at 0x1a21c640b8>),
 ('14', <simhash.Simhash at 0x1a21c64da0>),
 ('15', <simhash.Simhash at 0x1a21c64d30>),
 ('16', <simhash.Simhash at 0x10b33a630>),
 ('17', <simhash.Simhash at 0x1a21c26b38>),
 ('18', <simhash.Simhash at 0x1a21c26978>),
 ('19', <simhash.Simhash at 0x1a21c26fd0>),
 ('20', <simhash.Simhash at 0x1a1be5d898>),
 ('21', <simhash.Simhash at 0x1a1be5d9b0>),
 ('22', <simhash.Simhash at 0x1a1be5d940>),

In [13]:
len(objs)

10300

## the output of the simhash from above should make the unique titles and so length of objs, with addition of 20 more articles, should go from 10320 to 10300

# In this section, I use generate a hash for each article title, and generate duplicates using index.get_near_dups

# I then access only one of the duplicate values, using .pop(0)


# I then append that popped index, and its corresponding Title, to a blank dictionary

# John Notes - sort the simhash by title 

# before 

# John notes - Can do this but unneccesary and probably didnt work

In [14]:
class my_dictionary(dict): 
  
    # __init__ function 
    def __init__(self): 
        self = dict() 
          
    # Function to add key:value 
    def add(self, key, value): 
        self[key] = value 

dict_obj = my_dictionary()        


for i in range(len(object1)):
    feed_sel = object1[i]
    feed_hash = Simhash(str(feed_sel['title']))
    dup_indices = index.get_near_dups(feed_hash)
    de_duped_index = dup_indices.pop(0)
    dict_obj.add(int(de_duped_index),object1[int(de_duped_index)]['title'].rstrip())
    
    #dict_obj.add(object1[i]['title'].rstrip(),output)

Big bucket found. key:11:0, len:245
Big bucket found. key:6:1, len:278
Big bucket found. key:18:2, len:415
Big bucket found. key:17:3, len:270
Big bucket found. key:1d:4, len:423
Big bucket found. key:9:5, len:350
Big bucket found. key:12:6, len:398
Big bucket found. key:4:7, len:255
Big bucket found. key:1:8, len:340
Big bucket found. key:e:9, len:220
Big bucket found. key:1e:0, len:769
Big bucket found. key:13:1, len:987
Big bucket found. key:10:2, len:1038
Big bucket found. key:10:3, len:758
Big bucket found. key:f:4, len:765
Big bucket found. key:16:5, len:715
Big bucket found. key:3:6, len:965
Big bucket found. key:13:7, len:909
Big bucket found. key:9:8, len:745
Big bucket found. key:0:9, len:824
Big bucket found. key:3a60:a, len:485
Big bucket found. key:6:0, len:388
Big bucket found. key:1:1, len:439
Big bucket found. key:11:2, len:497
Big bucket found. key:9:3, len:293
Big bucket found. key:14:4, len:359
Big bucket found. key:8:5, len:441
Big bucket found. key:9:6, len:326
Big

Big bucket found. key:12:3, len:353
Big bucket found. key:4:4, len:263
Big bucket found. key:1c:5, len:398
Big bucket found. key:14:6, len:282
Big bucket found. key:1f:7, len:424
Big bucket found. key:9:8, len:745
Big bucket found. key:5:9, len:305
Big bucket found. key:6:0, len:388
Big bucket found. key:1:1, len:439
Big bucket found. key:11:2, len:497
Big bucket found. key:9:3, len:293
Big bucket found. key:14:4, len:359
Big bucket found. key:8:5, len:441
Big bucket found. key:9:6, len:326
Big bucket found. key:b:7, len:340
Big bucket found. key:c:8, len:322
Big bucket found. key:d:9, len:326
Big bucket found. key:7:1, len:319
Big bucket found. key:3:2, len:275
Big bucket found. key:1b:3, len:606
Big bucket found. key:1e:4, len:248
Big bucket found. key:4:5, len:382
Big bucket found. key:4:6, len:323
Big bucket found. key:0:7, len:285
Big bucket found. key:1a:8, len:237
Big bucket found. key:10:9, len:288
Big bucket found. key:1:0, len:425
Big bucket found. key:4:1, len:385
Big bucket

Big bucket found. key:c:5, len:362
Big bucket found. key:19:7, len:315
Big bucket found. key:10:8, len:409
Big bucket found. key:13:9, len:344
Big bucket found. key:0:0, len:598
Big bucket found. key:1d:1, len:303
Big bucket found. key:8:2, len:354
Big bucket found. key:0:3, len:248
Big bucket found. key:16:4, len:227
Big bucket found. key:9:5, len:350
Big bucket found. key:11:6, len:284
Big bucket found. key:18:7, len:288
Big bucket found. key:10:8, len:409
Big bucket found. key:1a:9, len:258
Big bucket found. key:5:0, len:277
Big bucket found. key:12:1, len:421
Big bucket found. key:d:2, len:308
Big bucket found. key:8:3, len:356
Big bucket found. key:d:4, len:323
Big bucket found. key:1c:5, len:398
Big bucket found. key:f:6, len:320
Big bucket found. key:6:7, len:238
Big bucket found. key:2:8, len:444
Big bucket found. key:15:9, len:241
Big bucket found. key:d:0, len:254
Big bucket found. key:17:2, len:275
Big bucket found. key:1f:3, len:446
Big bucket found. key:15:4, len:421
Big b

Big bucket found. key:11:2, len:497
Big bucket found. key:13:3, len:299
Big bucket found. key:11:4, len:453
Big bucket found. key:16:5, len:715
Big bucket found. key:8:7, len:246
Big bucket found. key:15:8, len:282
Big bucket found. key:1:9, len:377
Big bucket found. key:1:0, len:425
Big bucket found. key:1:1, len:439
Big bucket found. key:13:3, len:299
Big bucket found. key:15:4, len:421
Big bucket found. key:11:5, len:271
Big bucket found. key:10:6, len:291
Big bucket found. key:1b:7, len:417
Big bucket found. key:1d:8, len:234
Big bucket found. key:4:9, len:293
Big bucket found. key:1:0, len:425
Big bucket found. key:12:1, len:421
Big bucket found. key:4:2, len:266
Big bucket found. key:b:3, len:473
Big bucket found. key:d:4, len:323
Big bucket found. key:1c:5, len:398
Big bucket found. key:7:7, len:314
Big bucket found. key:1c:8, len:333
Big bucket found. key:0:9, len:824
Big bucket found. key:3:0, len:386
Big bucket found. key:3:1, len:277
Big bucket found. key:10:2, len:1038
Big 

Big bucket found. key:7:2, len:296
Big bucket found. key:17:3, len:270
Big bucket found. key:1f:4, len:335
Big bucket found. key:5:5, len:255
Big bucket found. key:b:6, len:250
Big bucket found. key:e:7, len:233
Big bucket found. key:15:8, len:282
Big bucket found. key:a:9, len:376
Big bucket found. key:5:0, len:277
Big bucket found. key:2:1, len:345
Big bucket found. key:1a:2, len:265
Big bucket found. key:1f:3, len:446
Big bucket found. key:f:4, len:765
Big bucket found. key:4:5, len:382
Big bucket found. key:6:6, len:292
Big bucket found. key:9:7, len:351
Big bucket found. key:9:8, len:745
Big bucket found. key:e:9, len:220
Big bucket found. key:1e:0, len:769
Big bucket found. key:13:1, len:987
Big bucket found. key:10:2, len:1038
Big bucket found. key:10:3, len:758
Big bucket found. key:f:4, len:765
Big bucket found. key:16:5, len:715
Big bucket found. key:3:6, len:965
Big bucket found. key:13:7, len:909
Big bucket found. key:9:8, len:745
Big bucket found. key:0:9, len:824
Big buck

...

Big bucket found. key:6:5, len:301
Big bucket found. key:14:6, len:282
Big bucket found. key:17:7, len:276
Big bucket found. key:3:8, len:262
Big bucket found. key:16:9, len:255
Big bucket found. key:5:0, len:277
Big bucket found. key:19:1, len:284
Big bucket found. key:9:2, len:326
Big bucket found. key:1c:3, len:317
Big bucket found. key:7:4, len:248
Big bucket found. key:19:5, len:358
Big bucket found. key:1a:6, len:314
Big bucket found. key:6:7, len:238
Big bucket found. key:15:8, len:282
Big bucket found. key:9:9, len:418
Big bucket found. key:e:0, len:232
Big bucket found. key:19:1, len:284
Big bucket found. key:16:2, len:259
Big bucket found. key:2:3, len:242
Big bucket found. key:13:4, len:379
Big bucket found. key:1d:5, len:263
Big bucket found. key:17:7, len:276
Big bucket found. key:16:8, len:375
Big bucket found. key:9:9, len:418
Big bucket found. key:2:0, len:541
Big bucket found. key:1e:1, len:224
Big bucket found. key:14:2, len:359
Big bucket found. key:9:4, len:234
Big 

Big bucket found. key:1e:8, len:256
Big bucket found. key:18:9, len:347
Big bucket found. key:13:0, len:250
Big bucket found. key:9:1, len:264
Big bucket found. key:0:2, len:402
Big bucket found. key:10:4, len:303
Big bucket found. key:12:5, len:252
Big bucket found. key:19:6, len:242
Big bucket found. key:14:7, len:285
Big bucket found. key:4:8, len:450
Big bucket found. key:13:9, len:344
Big bucket found. key:c:0, len:301
Big bucket found. key:2:1, len:345
Big bucket found. key:5:2, len:333
Big bucket found. key:1c:3, len:317
Big bucket found. key:1f:4, len:335
Big bucket found. key:7:5, len:306
Big bucket found. key:1:6, len:471
Big bucket found. key:b:7, len:340
Big bucket found. key:2:8, len:444
Big bucket found. key:15:9, len:241
Big bucket found. key:19:0, len:234
Big bucket found. key:0:1, len:415
Big bucket found. key:13:3, len:299
Big bucket found. key:a:4, len:211
Big bucket found. key:5:5, len:255
Big bucket found. key:6:6, len:292
Big bucket found. key:14:7, len:285
Big bu

Big bucket found. key:f:6, len:320
Big bucket found. key:1d:7, len:377
Big bucket found. key:4:8, len:450
Big bucket found. key:7:9, len:379
Big bucket found. key:0:0, len:598
Big bucket found. key:16:1, len:431
Big bucket found. key:9:2, len:326
Big bucket found. key:1b:3, len:606
Big bucket found. key:1a:4, len:289
Big bucket found. key:2:5, len:336
Big bucket found. key:13:6, len:378
Big bucket found. key:17:7, len:276
Big bucket found. key:1a:8, len:237
Big bucket found. key:15:9, len:241
Big bucket found. key:8:0, len:438
Big bucket found. key:11:1, len:469
Big bucket found. key:11:2, len:497
Big bucket found. key:e:3, len:366
Big bucket found. key:1a:4, len:289
Big bucket found. key:10:5, len:409
Big bucket found. key:0:6, len:679
Big bucket found. key:18:7, len:288
Big bucket found. key:0:8, len:463
Big bucket found. key:16:9, len:255
Big bucket found. key:5:0, len:277
Big bucket found. key:6:1, len:278
Big bucket found. key:11:2, len:497
Big bucket found. key:1:3, len:208
Big b

Big bucket found. key:c:9, len:270
Big bucket found. key:c:0, len:301
Big bucket found. key:3:1, len:277
Big bucket found. key:11:2, len:497
Big bucket found. key:1e:3, len:451
Big bucket found. key:19:4, len:351
Big bucket found. key:1e:5, len:219
Big bucket found. key:11:6, len:284
Big bucket found. key:1e:7, len:286
Big bucket found. key:9:8, len:745
Big bucket found. key:8:9, len:417
Big bucket found. key:a:0, len:422
Big bucket found. key:8:1, len:221
Big bucket found. key:3:2, len:275
Big bucket found. key:12:3, len:353
Big bucket found. key:d:4, len:323
Big bucket found. key:1f:5, len:208
Big bucket found. key:2:6, len:656
Big bucket found. key:1a:7, len:345
Big bucket found. key:0:8, len:463
Big bucket found. key:0:9, len:824
Big bucket found. key:11:0, len:245
Big bucket found. key:1:1, len:439
Big bucket found. key:0:2, len:402
Big bucket found. key:13:3, len:299
Big bucket found. key:6:4, len:243
Big bucket found. key:19:5, len:358
Big bucket found. key:1a:6, len:314
Big buc

Big bucket found. key:16:0, len:235
Big bucket found. key:d:1, len:234
Big bucket found. key:5:2, len:333
Big bucket found. key:2:3, len:242
Big bucket found. key:11:4, len:453
Big bucket found. key:12:5, len:252
Big bucket found. key:1:7, len:345
Big bucket found. key:19:8, len:253
Big bucket found. key:10:9, len:288
Big bucket found. key:f:0, len:244
Big bucket found. key:1:1, len:439
Big bucket found. key:13:2, len:332
Big bucket found. key:1:4, len:292
Big bucket found. key:0:5, len:438
Big bucket found. key:12:6, len:398
Big bucket found. key:1:7, len:345
Big bucket found. key:3:8, len:262
Big bucket found. key:9:9, len:418
Big bucket found. key:f:0, len:244
Big bucket found. key:5:1, len:370
Big bucket found. key:3:2, len:275
Big bucket found. key:4:4, len:263
Big bucket found. key:0:5, len:438
Big bucket found. key:2:6, len:656
Big bucket found. key:1:7, len:345
Big bucket found. key:3:8, len:262
Big bucket found. key:8:9, len:417
Big bucket found. key:2:0, len:541
Big bucket fo

In [15]:
print("Length of original dictionary:",len(object1),"vs","length of de_duped_dict:",len(dict_obj))

Length of original dictionary: 10300 vs length of de_duped_dict: 6633


# Considering the above, it appears that our new dictionary object has significantly less articles". Below code will make sure that no duplicative values exist

In [16]:
len(set(dict_obj.items()))

6633

In [17]:
dict_obj

{0: 'BHP reviews lobby group membership amid investor climate push',
 8034: '',
 107: 'US, Chinese envoys to meet in October for tariff war talks',
 5: 'Boxwood Merger, Atlas Technical Consultants combine businesses',
 6: 'OCC Fined by SEC/CFTC; CME’s Bitcoin Options(?!)',
 7: 'Industry bill for PPI claims could hit £53bn',
 9: 'Markets surge as China, US agree to hold trade talks next month',
 10: 'Uber’s Nightmare Has Just Started',
 11: 'Messi può lasciare il Barcellona gratis alla fine della prossima stagione',
 12: '8 Ways to Play the Market Before the Next Stock Correction',
 13: 'Stocks Climb After Trade Talks News',
 6508: 'Top 5 Things to Know in the Market on Thursday - Investing.com',
 15: 'US President Donald Trump says Dow stock index would be 10000 points higher without trade war - Gulf News',
 16: 'Treasury Yields Surge With Stocks After China Hoodwinks Investors – Accu-rate',
 17: 'This Little Noticed S&P Index Is Up 25% This Year—and Offers a Hedge Against Wild Market 

In [18]:
with open('apan_5430_deduped_corpus_titles.pickle', 'wb') as handle:
    pickle.dump(dict_obj, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('apan_5430_deduped_corpus_titles.pickle', 'rb') as handle:
    b = pickle.load(handle)

In [22]:
import pandas as pd
df_feeds = pd.DataFrame(list(dict_obj.items()))

In [23]:
df_feeds.columns = ['old_index', 'title']

In [24]:
df_feeds.to_pickle('apan_5430_deduped_corpus_titles_df.pickle') 

In [19]:
b

{0: 'BHP reviews lobby group membership amid investor climate push',
 8034: '',
 107: 'US, Chinese envoys to meet in October for tariff war talks',
 5: 'Boxwood Merger, Atlas Technical Consultants combine businesses',
 6: 'OCC Fined by SEC/CFTC; CME’s Bitcoin Options(?!)',
 7: 'Industry bill for PPI claims could hit £53bn',
 9: 'Markets surge as China, US agree to hold trade talks next month',
 10: 'Uber’s Nightmare Has Just Started',
 11: 'Messi può lasciare il Barcellona gratis alla fine della prossima stagione',
 12: '8 Ways to Play the Market Before the Next Stock Correction',
 13: 'Stocks Climb After Trade Talks News',
 6508: 'Top 5 Things to Know in the Market on Thursday - Investing.com',
 15: 'US President Donald Trump says Dow stock index would be 10000 points higher without trade war - Gulf News',
 16: 'Treasury Yields Surge With Stocks After China Hoodwinks Investors – Accu-rate',
 17: 'This Little Noticed S&P Index Is Up 25% This Year—and Offers a Hedge Against Wild Market 

In [122]:
for key in dict_obj.keys():
    if item in dict_obj[key]:
        print(key)

1964
2256


# Keep this for sure and also do sorted above

# highlight the differences 

# i

In [63]:
rev_multidict = {}
for key, value in dict_obj.items():
    rev_multidict.setdefault(value, set()).add(key)
    
[key for key, values in rev_multidict.items() if len(values) > 1]

['Trump has a favorite number when he makes big claims: 10,000',
 'Ram Jethmalani passes away in Delhi, cremated',
 'GLOBAL MARKETS-Stocks gain on stimulus hopes, pound hits 6-week high By Reuters',
 'US STOCKS-Stimulus hopes buoy Wall Street, financials lead gains',
 'BP (BP) Outpaces Stock Market Gains: What You Should Know',
 'Trump Delays Increase In China Tariffs Until October 15; Futures Surge',
 'GLOBAL MARKETS-Trade hopes lifts stocks, bond yields',
 'Peyto Exploration & Development Corp. Confirms Dividends for October 15, 2019',
 'Saudi, Gulf stocks fall after attacks on Aramco oil plants']

In [64]:
[values for key, values in rev_multidict.items() if len(values) > 1]

[{891, 2256},
 {2266, 2551},
 {2841, 2891},
 {3037, 4925},
 {4395, 4610},
 {5793, 5832},
 {7009, 7467},
 {8257, 8564},
 {9494, 9597}]

In [72]:
from itertools import chain
print(set(chain.from_iterable(values for key, values in rev_multidict.items() if len(values) > 1)))
print("number of still duped articles:",len(set(chain.from_iterable(values for key, values in rev_multidict.items() if len(values) > 1))))

{5793, 4610, 7009, 8257, 5832, 9597, 2891, 4925, 4395, 7467, 2256, 8564, 9494, 2551, 2841, 2266, 891, 3037}
number of still duped articles: 18


# Unfortunately, it looks like the pop(0) method did not result in a completley de-duped set of articles

# there are still 9 (or half of 18) that should be removed. 

# As discussed in my email, I was uncertain of how to proceed here and requested help from John in the afternoon of Oct 23 and Oct 24

# I further had trouble using word_2_vec on top of LSH.

# Rationale for function below: 

### The idea behind the below function was to iterate through each article from the de_duped corpus above, and calculate its semantic similarity with the other articles in the corpus. Similar to above, I set the threshold at a high value of .97 because I wanted to be careful not to de_dupe small differences that may seem semantically similar, but are not given the domain of financial markets. 

# I ultimately wanted to store everything in a new dictionary, and take out values where there was an extremely high semantic value. Unfortunately I did not get this far, as the program took too long to run. I have a sample provided below

In [127]:
class my_dictionary(dict): 
  
    # __init__ function 
    def __init__(self): 
        self = dict() 
          
    # Function to add key:value 
    def add(self, key, value): 
        self[key] = value 

dict_obj_new = my_dictionary()        


def more_sim_v2v(dict1,dict2):

    
    for i in dict1.keys():
        for j in dict2.keys():
            try:
                if dict1[i] != dict2[j]:
                    score = calc_similarity(dict1[i],dict2[j],model_w2v_AP)

                    if score > .97:
                        dict_obj_new.add(score,[[i,dict1[i].rstrip()],[j,dict2[j].rstrip()]])
                    elif score <.97:
                        pass
                elif dict1[i] == dict2[j]:
                    pass
            except:
                pass
    return dict_obj_new




In [128]:
test3 = dict((k, dict_obj[k]) for k in (0,9719, 258, 5, 6, 7, 9, 10, 11, 12, 13, 6508, 15, 297, 483, 18, 42, 21, 22, 23, 25, 26, 27, 28, 29, 30, 31, 321, 34, 91, 232, 37, 38, 39, 44, 45, 46, 191, 48, 49, 99, 51, 52, 53, 54, 55, 56, 58, 209, 60, 61, 62, 63, 64, 66, 67, 68, 69, 8278, 71, 72, 73, 74, 5923, 76, 77, 78, 79, 81, 187, 92, 7073, 96, 98, 100, 117, 1603, 109, 111, 112, 113, 114, 116, 119, 120, 121, 3331, 123, 124, 125, 126, 127, 128, 408, 452, 133, 134, 135, 137, 140, 142, 143, 329, 5719, 146, 147, 334, 149, 150, 151, 152, 153, 154, 155, 156, 158, 159, 160, 161, 162, 163, 164, 3968, 166, 167, 227, 169, 170, 171, 172, 211, 177, 179, 180, 186, 188, 189, 194, 195, 197, 214, 972, 6676, 204, 210, 212, 213, 1910, 216, 217, 218, 219, 220, 221, 222, 267, 366, 441, 231, 233, 234, 235, 395, 238, 240, 242, 244, 245, 1135, 247, 248, 249, 251, 252, 351, 1565, 8908, 263, 310, 265, 311, 270, 271, 272, 274, 275, 277, 278, 279, 280, 281, 282, 283, 339, 286, 419, 288, 289, 290, 291, 292, 293, 294, 295, 296, 298, 300, 301, 304, 305, 306, 307, 308, 309, 313, 314, 315, 316, 317, 318, 319, 320, 322, 323, 324, 428, 836, 327, 1455, 1669, 338, 340, 341, 342, 343, 344, 345, 346, 348, 350, 352, 353, 354, 356, 359, 360, 362, 367, 373, 374, 375, 376, 377, 378, 379, 503, 381, 382, 383, 384, 385, 386, 387, 520, 595, 2177, 517, 393, 394, 397, 400, 401, 402, 403, 7599, 406, 407, 410, 411, 412, 413, 414, 415, 417, 1563, 421, 423, 810, 426, 427, 429, 432, 434, 436, 437, 663, 439, 518, 443, 444, 445, 446, 447, 448, 449, 450, 1111, 453, 456, 457, 458, 548, 462, 463, 464, 465, 1534, 467, 481, 471, 472, 473, 474, 475, 476, 477, 478, 479, 480, 482, 484, 485, 487, 539, 489, 493, 495, 500, 501, 620, 506, 507, 508, 509, 511, 513, 514, 515, 516, 519, 521, 523, 527, 504, 532, 533, 535, 536, 537, 538, 542, 543, 544, 725, 547, 550, 552, 553, 555, 556, 557, 558, 560, 561, 563, 564, 566, 567, 568, 569, 570, 798, 572, 604, 574, 575, 576, 581, 583, 586, 587, 588, 589, 727, 592, 593, 771, 820, 821, 601, 602, 603, 606, 607, 610, 611, 612, 613, 614, 615, 616, 617, 618, 621, 624, 625, 626, 2394, 628, 718, 631, 632, 633, 634, 635, 636, 637, 1018, 639, 640, 642, 643, 644, 645, 646, 974, 648, 649, 650, 651, 652, 653, 654, 655, 656, 657, 926, 660, 6459, 662, 665, 666, 667, 669, 1034, 671, 672, 674, 675, 676, 677, 678, 3810, 680, 681, 682, 683, 684, 685, 686, 687, 688, 689, 690, 691, 692, 695, 696, 1898, 698, 699, 700, 701, 702, 703, 704, 705, 706, 707, 708, 709, 710, 715, 1580, 2633, 1581, 722, 723, 726, 729, 730, 731, 733, 734, 735, 736, 737, 738, 739, 740, 741, 742, 743, 3449, 745, 746, 747, 748, 749, 750, 751, 752, 753, 756, 757, 758, 759, 760, 811, 775, 766, 1233, 778, 769, 768, 773, 774, 776, 777, 779, 781, 782, 783, 784, 786, 787, 788, 1205, 790, 792, 793, 794, 1090, 1844, 1493, 801, 803, 806, 807, 6623, 1256, 813, 815, 816, 817, 818, 819, 822, 823, 824, 825, 826, 842, 551, 1194, 7877, 834, 839, 840, 843, 844, 848, 850, 866, 852, 854, 855, 856, 860, 861, 862, 863, 864, 865, 867, 868, 879, 870, 1964, 872, 873, 874, 875, 876, 877, 878, 880, 881, 882, 884, 886, 887, 888, 889, 890, 2256, 892, 894, 895, 896, 898, 902, 903, 904, 1258, 1397, 907, 908, 909, 910, 952, 912, 921, 915, 917, 919, 920, 928, 924, 927, 930, 932, 933, 934, 935, 971, 939, 940, 941, 942, 943, 1650, 945, 946, 947, 948, 949, 950, 951, 953, 954, 955, 956, 997, 961, 963, 964, 5755, 968, 970, 975, 976, 979, 981, 1457, 983, 984, 985, 1021, 987, 988, 989, 990, 991, 992, 993, 994, 1516, 996, 1141, 1373, 1004, 1005, 1006, 1007, 1008, 1009, 1010, 1011, 1013, 1014, 1015, 1016, 1017, 1019, 1020, 1022, 1023, 1024, 1025, 1026, 1027, 6526, 1029, 1030, 1031, 1032, 1033, 1035, 1036, 1037, 1038, 1039, 1040, 1041, 1042, 1043, 1044, 1045, 1046, 1047, 1048, 1049, 1189, 1052, 1053, 1054, 1055, 1056, 1430, 1060, 1061, 1062, 1063, 1064, 1065, 1066, 1067, 1068, 1069, 8440, 1071, 1072, 1075, 8185, 1077, 1078, 1208, 1092, 1083, 1085, 1086, 1087, 1088, 1089, 1091, 1093, 1095, 1096, 1097, 1098, 1099))

In [129]:
print("length of test_example:",len(test3))

length of test_example: 772


In [130]:
test4=test3

In [131]:
more_sim_v2v(test3,test4)

{1.0: [[8440,
   '5 things to know before the stock market opens September 13, 2019'],
  [304, '5 things to know before the stock market opens September 5, 2019']],
 0.97790533: [[179,
   'REFILE-UPDATE 3-China, U.S. to hold trade talks in Oct; Beijing says phone call went well'],
  [191,
   'China, US to hold trade talks in October; Beijing says phone call went well']],
 0.98933345: [[465,
   'Plans for new US-China trade talks boost US stock indexes | | billingsgazette.com'],
  [227, 'Plans for new US-China trade talks boost US stock indexes']],
 0.97723806: [[376, 'Italy PM Conte Unveils New Government'],
  [204, 'Italy PM Conte Launches New Government']],
 0.9824872: [[401,
   'Top 10 fastest-growing companies listed on US stock market - Chinadaily.com.cn'],
  [317, 'Top 10 fastest-growing companies listed on US stock market']],
 0.9707506: [[674,
   'Hong Kong withdraws extradition bill that sparked protests | Nation/World News | heraldandnews.com'],
  [503, 'Hong Kong withdraws e

# De_duping using semantic scores programatically proves to be tricky, as the algorithm ranked the below articles with a similarity score of 1, but they represent different days

1.0: [[8440,
   '5 things to know before the stock market opens September 13, 2019'],
  [304, '5 things to know before the stock market opens September 5, 2019']]


# John Notes - word2vec is based on index hashing so for every word we have an index... LSH is an algo that for each article, we dudplicate based on title 

# but it's not a word vector based deduplication.... on top of LSH, but dones't have to be word2vec 

# simhash de dupes articles based on titles 

# so for where professor includes for loop iterating through dup indices.... so im gonna have two dicts - one original by title and one dedupded dictionary and we have word2vec model 

# prof's code is aiming to look at score 

## john notes - so the results should show that for original dict of 10320, and deduped dict of 10300 (20 dupes removed).... iterate through 10320 and show using word2vec, show that using a threshold it will remove dupes 

## threshold should remove similar articles with just a "-" or ":" difference

## so still going ot have to go through both deduped and original ... around 1mm times 



### lets say from lsh we found 20 duplicates.... those 20 duplicates may be matches at the "-" level........ theoretically we can add w2v on top of those 20, and then remove the 20 + whatever word2vec adds ontop of it 




In [ ]:
count_dup = 0
for dupi in dup_indices:
    try:
        score = calc_similarity(feed_sel['title'], feeds[int(dupi)]['title'], model_w2v_AP)
    except:
        score = 0
    if score > 0.5:
        count_dup += 1
        print(feeds[int(dupi)]['title'])
print("Number of Dupies (SimHash + WordVectors): " + str(count_dup))

# Json Storage  and Reading back in

In [142]:
import json
r = json.dumps(dict_obj)

with open('apan_5430_deduped_corpus.txt', 'w') as outfile:
    json.dump(r, outfile)


loaded_r = json.loads(r)
print("length of corpus:",len(loaded_r), 'articles')

length of corpus: 6628 articles
